In [1]:
# Everything except adaptive will probably work fine with other versions as well. 

# Python 3.6.6
import itertools
import random

# ipywidgets 7.4.1
from ipywidgets import interact_manual

# Numpy 1.15.1
import numpy as np

# Scipy 1.1.0
import scipy
import scipy.linalg
import scipy.spatial


# Kwant 1.3.3. May work with lower versions as well, I didn't test this
from kwant import builder, system, plotter
from kwant.linalg import lll
from kwant.builder import herm_conj, HermConjOfFunc
from kwant.lattice import TranslationalSymmetry
from kwant._common import get_parameters
from kwant.wraparound import *
import kwant.linalg
import kwant.lattice

# Adaptive 0.6 branch [111-no-flat-simplices], it doesn't work with on the master branch
import adaptive
adaptive.notebook_extension()


In [3]:
# Define the lattice vectors of some common unit cells
# Hexagonal
a = -np.pi/6
unit_cell_vectors_hexagonal = [
    (        0,         1, 0), 
    (np.cos(a), np.sin(a), 0), 
    (        0,         0, 1)
]

# Simple cubic
unit_cell_vectors_simple_cubic = [
    (1, 0, 0), 
    (0, 1, 0), 
    (0, 0, 1)
]

# FCC
unit_cell_vectors_fcc = [
    (0,.5,.5), 
    (.5,.5,0), 
    (.5,0,.5)
]

# BCC
unit_cell_vectors_bcc = [
    (-.5, .5, .5), 
    ( .5,-.5, .5), 
    ( .5, .5,-.5)
]

In [4]:
# Choose some latice and atoms, like hexagonal in this case
unit_cell_vectors = unit_cell_vectors_hexagonal
unit_cell_atoms = [
    ( 0,  0,  0)
]

def create_syst():
    lat = kwant.lattice.Polyatomic(unit_cell_vectors, unit_cell_atoms, 'Some crystal')
   
    syst = kwant.Builder(kwant.TranslationalSymmetry(*lat.prim_vecs)) # infinite in all dimensions
    syst[lat.shape(lambda pos: True, (0, 0, 0))] = 6 # onsite
    syst[lat.neighbors()] = -1 # hopping

    syst = kwant.wraparound.wraparound(syst).finalized()

    
#     H = "k_x**2 + k_y**2 + k_z**2 + mu"
#     template = kwant.continuum.discretize(H, grid_spacing=a)
#     syst = kwant.wraparound.wraparound(template).finalized()
    
    return syst

syst = create_syst()

def energies(params):
    H = syst.hamiltonian_submatrix(params=params)
    eigs = np.linalg.eigvalsh(H)
    return eigs

In [5]:
# Do some math
B = np.asarray(unit_cell_vectors).T
A = np.linalg.pinv(B).T

neighbours = kwant.linalg.lll.voronoi(A)
lattice_points = np.concatenate(([[0,0,0]], neighbours))
lattice_points = 2 * np.pi * (lattice_points @ A.T)
vor = scipy.spatial.Voronoi(lattice_points)
brillouin_zone = vor.vertices[vor.regions[vor.point_region[0]]]
hull = scipy.spatial.ConvexHull(brillouin_zone)

bounds = list(map(tuple, np.vstack([
    np.min(brillouin_zone, axis=0),
    np.max(brillouin_zone, axis=0)
]).T * (1+1e-6))) # make bounds

In [10]:
# convertion of coordinate system
def momentum_to_lattice(k):
    k, residuals = scipy.linalg.lstsq(A, k)[:2]
    if np.any(abs(residuals) > 1e-7):
        raise RuntimeError("Requested momentum doesn't correspond"
                           " to any lattice momentum.")
    return k

# Get the energy for a given k-vector
def E(k):
    k_x, k_y, k_z = momentum_to_lattice(k)
    return min(energies({'k_x': k_x, 'k_y': k_y, 'k_z': k_z}))

In [11]:
v = [1,0,0]
print(momentum_to_lattice(v))
print(B.T @ v)

[-3.69482948e-17  8.66025404e-01  0.00000000e+00]
[0.        0.8660254 0.       ]


In [12]:

if True:
    # Now do some adaptive, remember E = E(k)
    learner = adaptive.LearnerND(E, hull)

    # Get some points
    runner = adaptive.Runner(learner, goal=lambda l: l.npoints > 5000) 
    runner.live_info()

In [13]:
# Click `run interact` to run show some iso surface every time you change the value
def iso(level=8):
    return learner.plot_isosurface(level=level, hull_opacity=0.2)

min_level = round(min(learner.values) + 0.1, 1)
max_level = round(max(learner.values) - 0.1, 1)

interact_manual(iso, level=(min_level, max_level, 0.1)) 
# Notice the color conveys no meaning, it is colorod based on the z-coordinate only
# iso(7)

interactive(children=(FloatSlider(value=8.0, description='level', max=10.9, min=-1.9), Button(description='Run…

<function __main__.iso(level=8)>

In [14]:
learner.plot_isosurface(level=6.5, hull_opacity=0.2)